# Add MLOps to existing code

This tutorial showcases how easy it is to apply MLRun on your existing code. With only 7 lines of code, you get:
* Experiment tracking &mdash; Track every single run of your experiment to learn what yielded the best results.
* Automatic Logging &mdash; Log datasets, metrics results and plots with one line of code. MLRun takes care for all the rest.
* Parameterization &mdash; Enable running your code with different parameters, run hyperparameters tuning and get the most out of your code.
* Resource management &mdash; Control the amount of resources available for your experiment.

Use this [kaggle code](https://www.kaggle.com/code/jsylas/python-version-of-top-ten-rank-r-22-m-2-88/script) by [Sylas](https://www.kaggle.com/jsylas) as an example, part of the competition [New York City Taxi Fare Prediction](https://www.kaggle.com/competitions/new-york-city-taxi-fare-prediction/overview/description).

Tutorial steps:
- [**Get the data**](#get-data)
- [**Code review**](#code-review)
- [**Run the script with MLRun**](#run-script)
- [**Review outputs**](#review-outputs)

<a id="get-data"></a>
## Get the data

You can download the original data from [kaggle](https://www.kaggle.com/code/jsylas/python-version-of-top-ten-rank-r-22-m-2-88/data?select=train.csv). However, since the original data is 5.7GB in size, this demo uses sampled data. Since this demo uses MLRun's `DataItem` to pass the datasets, the sampled data is downloaded automatically. However, if you want to look at the data, you can download it: [training set](https://s3.us-east-1.wasabisys.com/iguazio/data/nyc-taxi/train.csv), and [testing set](https://s3.us-east-1.wasabisys.com/iguazio/data/nyc-taxi/test.csv).

<a id="code-review"></a>
## Code review

Use the original code with the **minimum** changes required to apply MLRun to it. The code itself is straightforward:
1. Read the training data and perform feature engineering on it to preprocess it for training.
2. Train a LightGBM regression model using LightGBM's `train` function.
3. Read the testing data and save the contest expected submission file.

You can [**Download the `script.py` file**](./src/script.py)**{Download}`[Download here]<./src/script.py>`**, or copy / paste it from here:
````{dropdown} Show code
   ```{literalinclude} ./src/script.py
   :language: python3
   ```
````

This demo focuses on reviewing the changes / additions made to the original code so that you can apply MLRun on top of it. **Seven lines of code are added / replaced** as you can see in the sections below:

### Initialization

#### Imports

On lines 9-10, add 2 imports:
* `mlrun` &mdash; Import MLRun of course.
* `apply_mlrun` &mdash; Use the `apply_mlrun` function from MLRun's frameworks, a sub-package for common ML/DL frameworks integrations with MLRun. 

```python
import mlrun
from mlrun.frameworks.lgbm import apply_mlrun
```

#### MLRun context

To get parameters and inputs into the code, you need to get MLRun's context. Use the function `get_or_create_ctx`.

Line 13:
```python
context = mlrun.get_or_create_ctx("apply-mlrun-tutorial")
```

#### Get Training Set

In the original code the training set was read from a local file. Now you want to get it from the user who runs the code. 
Use the context to get the `"training_set"` input by using the `get_input` method. To maintain the original logic, include the default path for when the training set was not provided by the user.

Line 16:
```python
train_df = context.get_input("train_set", "./train.csv").as_df()  
# Instead of: `train_df =  pd.read_csv('./train.csv')`
```


### Apply MLRun

Now use the `apply_mlrun` function from MLRun's LightGBM framework integration. MLRun automatically wraps the LightGBM module and enables automatic logging and evaluation.

Line 209:
```python
apply_mlrun(context=context)
```

### Logging the dataset

Similar to the way you got the training set, you get the test dataset as an input from the MLRun content.

Line 226:
```python
test_df = context.get_input("test_set", "./test.csv").as_df()
# Instead of: `test_df =  pd.read_csv('./test.csv')`
```

#### Save the submission

Finally, instead of saving the result locally, log the submission to MLRun.

Line 258:
```python
context.log_dataset(key="taxi_fare_submission", df=submission, format="csv")  
# Instead of: `submission.to_csv('taxi_fare_submission.csv',index=False)`
```


<a id="run-script"></a>
## Run the script with MLRun

Now you can run the script and see MLRun in action.

In [2]:
import mlrun

### Create a project

Create a project using the function `get_or_create_project`. To read more about MLRun projects, see [Projects](https://docs.mlrun.org/en/latest/projects/project.html).

In [3]:
project = mlrun.get_or_create_project(
    name="apply-mlrun-tutorial", context="./", user_project=True
)

> 2022-08-09 18:21:26,785 [info] loaded project apply-mlrun-tutorial from MLRun DB


### Create a function

Create an MLRun function using the function `code_to_function`. To read more about MLRun functions, see [Functions](../runtimes/functions.html).

In [ ]:
script_function = mlrun.code_to_function(
    filename="./src/script.py",
    name="apply-mlrun-tutorial-function",
    kind="job",
    image="mlrun/mlrun",
    requirements=["lightgbm"],
)
script_function.deploy()

### Run the function

Now you can run the function, providing it with the inputs you want. Use the datasets links to send them to the function. MLRun downloads and reads them into `pd.DataFrame` automatically.

In [5]:
script_run = script_function.run(
    inputs={
        "train_set": "https://s3.us-east-1.wasabisys.com/iguazio/data/nyc-taxi/train.csv",
        "test_set": "https://s3.us-east-1.wasabisys.com/iguazio/data/nyc-taxi/test.csv",
    },
)

> 2022-08-09 18:21:26,851 [info] starting run apply-mlrun-tutorial-function uid=8d82ef16a15d4151a16060c13b133170 DB=http://mlrun-api:8080
> 2022-08-09 18:21:27,017 [info] handler was not provided running main (./script.py)
> 2022-08-09 18:21:39,330 [info] logging run results to: http://mlrun-api:8080
   pickup_longitude  pickup_latitude  ...  distance   bearing
0         -1.288826         0.710721  ...  1.030764 -2.918897
1         -1.291824         0.710546  ...  8.450134 -0.375217
2         -1.291242         0.711418  ...  1.389525  2.599961
3         -1.291319         0.710927  ...  2.799270  0.133905
4         -1.290987         0.711536  ...  1.999157 -0.502703

[5 rows x 17 columns]
[LightGBM] [Warning] bagging_fraction is set=1, subsample=0.8 will be ignored. Current value: bagging_fraction=1
[LightGBM] [Warning] Met categorical feature which contains sparse values. Consider renumbering to consecutive integers started from zero
[LightGBM] [Warning] bagging_fraction is set=1, subs

> 2022-08-09 18:22:02,987 [info] run executed, status=completed


<a id="review-outputs"></a>
## Review outputs

To view the outputs yielded by the MLRun automatic logging and evaluation, call the `outputs` property on the run object:

In [6]:
script_run.outputs

{'valid_0_rmse': 3.905279481685527,
 'valid_0_rmse_plot': 'v3io:///projects/apply-mlrun-tutorial-guyl/artifacts/apply-mlrun-tutorial-function/0/valid_0_rmse_plot.html',
 'valid_0-feature-importance': 'v3io:///projects/apply-mlrun-tutorial-guyl/artifacts/apply-mlrun-tutorial-function/0/valid_0-feature-importance.html',
 'valid_0': 'store://artifacts/apply-mlrun-tutorial-guyl/apply-mlrun-tutorial-function_valid_0:8d82ef16a15d4151a16060c13b133170',
 'model': 'store://artifacts/apply-mlrun-tutorial-guyl/model:8d82ef16a15d4151a16060c13b133170',
 'taxi_fare_submission': 'store://artifacts/apply-mlrun-tutorial-guyl/apply-mlrun-tutorial-function_taxi_fare_submission:8d82ef16a15d4151a16060c13b133170'}

MLRun **automatically detects all the metrics calculated** and collects the data along with the training. Here there was one validation set named `valid_0` and the RMSE metric was calculated on it. You can see the RMSE values per iteration plot and the final score including the features importance plot.

You can explore the different artifacts by calling the `artifact` function like this:

In [11]:
script_run.artifact("valid_0_rmse_plot").show()

In [10]:
script_run.artifact("valid_0-feature-importance").show()

And of course, you can also see the submission that was logged:

In [12]:
script_run.artifact("taxi_fare_submission").show()

key  fare_amount
0     2015-01-27 13:08:24.0000002    10.281408
1     2015-01-27 13:08:24.0000003    11.019641
2     2011-10-08 11:53:44.0000002     4.898061
3     2012-12-01 21:12:12.0000002     7.758042
4     2012-12-01 21:12:12.0000003    15.298775
...                           ...          ...
9909  2015-05-10 12:37:51.0000002     9.117569
9910  2015-01-12 17:05:51.0000001    10.850885
9911  2015-04-19 20:44:15.0000001    55.048856
9912  2015-01-31 01:05:19.0000005    20.110280
9913  2015-01-18 14:06:23.0000006     7.081041

[9914 rows x 2 columns]